# EPS109 Fall 2022 Final Project
# Simulating the Kepler-47 System
### Amrutha Kalle
There are no special requirements to run this code other than changing the `plt.Params` for `FFMPEG Writer` (line 4 in the first code block).

#### Background
The Kepler-47 planetary system is located in the constellation Cygnus about 3442 light years (about 2x10<sup>16</sup> miles) from Earth. It is notable for being one of the first systems discovered where there are multiple planets orbiting both stars.\
The Bodies
- 47A, a G-type main sequence star similar to our Sun
- 47B, a red dwarf about a third of the mass of 47A
- 47b, the Neptune-like inner planet
- 47c, the Neptune-like outer planet that is in the habitable zone
- 47d, the Neptune-like middle planet

I will approximate all of the eccentricities of planets' orbits to be 0, as they are actually very close to zero (47b - <0.035, 47c - <0.411, 47d - 0.024) and it will make the calculations easier. I will also only consider the forces between the planets and the primary star, and between the primary star and companion star as the planet-planet and planet-companion star forces are pretty small compared to interactions with the primary star.

I will use the definition of the habitable zone as the range of distances from the star where liquid water could exist on the surface of the planet, as stated in Orosz 2012 and Orosz 2019, the papers that detail the discovery of the system. To determine the exact boundries, I used the conditions listed in Doyle 1998:
- Inner radius: runaway greenhouse effect, where water vapor in the atmosphere is vaporized and lost into space. In the Solar System, this happens at $1.1S_{\odot}$, where $S_{\odot}$ is the solar flux at Earth.
- Outer radius: where CO<sub>2</sub> condensation starts taking place. In the Solar System, this happens at $0.53S_{\odot}$.

Althouh 47c is probably a gas giant and inhospitable to life, it is still an interesting case of a planet inside the classical habitable zone of a binary system.

Sources
- Orosz, J. A., W.F. Welsh, et. al., “Kepler-47: A Transiting Circumbinary Multi-Planet System,” Science, vol. 337, p. 1511, August 2012.
- Orosz, J. A., W. F. Welsh, et. al. “Discovery of a third transiting planet in the kepler-47 circumbinary system.” The Astronomical Journal, vol. 157, p. 174, April 2019.
- Doyle, L. R., J. Billingham, D. L. DeVincenzi, "Circumstellar habitable zones: an overview,", Acta Astronautica, vol. 42, p. 599-605, 1998.
- Haghighipour, N, and L. Kaltenegger, "Calculating the Habitable Zone of Binary Star Systems. II. P-Type Binaries," The Astrophysical Journal, vol. 777, p. 166, October 2013.

In [1]:
import numpy as np
import matplotlib.pyplot as plt
%config InlineBackend.figure_format='retina'
plt.rcParams['animation.ffmpeg_path']=r'C:\Program Files\ffmpeg\bin\ffmpeg.exe'
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Kepler-47', artist='Matplotlib', comment='idk')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
%matplotlib qt

In [2]:
###### CONSTANTS ######

#STAR MASSES (kg)
mS = 2E30           #Sun
mA = 1.043*mS       #47A
mB = 0.362*mS       #47B

#PLANET MASSES (kg)
mE = 6E24           #Earth
mb = 2.07*mE        #47b
mc = 3.17*mE        #47c
md = 19.2*mE        #47d

#DISTANCES (m)
AU = 1.5E11         #1 AU in meters
AB = 0.0836*AU      #distance between 47A and 47B
ab = 0.2877*AU      #semimajor axis = distance from center of mass
ac = 0.9638*AU 
ad = 0.6992*AU

#ORBITAL PERIODS (s)
day = 60*60*24      #1 day in seconds
pA = pB = 7.45*day  #orbital period of two stars
pb = 49.5*day
pc = 303*day
pd = 187*day

G = 6.67E-11        #gravitational constant (m^3/(kg*s^2))

#center of mass with 47B at (0, 0)
rcm = (mA*AB+mb*ab+md*ad+mc*ac)/(mB+mA+mb+mc+md)


#initial positions -> setting everything on the x-axis
rA = np.array([AB-rcm, 0])
rB = np.array([-rcm, 0])
rb = np.array([ab, 0])
rc = np.array([ac, 0])
rd = np.array([ad, 0])

#initial angular velocities -> estimating semi-major axis as distance from planet to primary star
wA = wB = np.sqrt(G*(mA+mB)/AB**3) #angular speed influenced by each other, not by planets
wb = np.sqrt(G*(mA+mb)/ab**3)
wc = np.sqrt(G*(mA+mc)/ac**3)
wd = np.sqrt(G*(mA+md)/ad**3)

#initial tangent velocities
vA = np.array([0, rA[0]*wA])
vB = np.array([0, rB[0]*wB])
vb = np.array([0, rb[0]*wb])
vc = np.array([0, rc[0]*wc])
vd = np.array([0, rd[0]*wd])

y0A = np.concatenate((rA, vA))
y0B = np.concatenate((rB, vB))
y0b = np.concatenate((rb, vb))
y0c = np.concatenate((rc, vc))
y0d = np.concatenate((rd, vd))
y0 = np.concatenate((y0A, y0B, y0b, y0c, y0d))

In [3]:
###### HELPER FUNCTION TO CALCULATE FORCE BETWEEN TWO BODIES ######
def Force(m1, m2, r1, r2):
    global G
    r = np.linalg.norm(r1-r2)
    return -m1*m2*G/r**3 * (r1-r2)

In [4]:
###### FUNCTION TO CALCULATE dx AND dv ######
def KeplerODE(t, y):
    global G, mA, mB, mb, mc, md
    rA = y[0:2]
    vA = y[2:4]
    rB = y[4:6]
    vB = y[6:8]
    rb = y[8:10]
    vb = y[10:12]
    rc = y[12:14]
    vc = y[14:16]
    rd = y[16:18]
    vd = y[18:20]
    
    #47A
    drA = vA
    dvA = Force(mA, mB, rA, rB)/mA
    
    #47B
    drB = vB
    dvB = Force(mB, mA, rB, rA)/mB
    
    #47b
    drb = vb
    dvb = Force(mb, mA, rb, rA)/mb
    
    #47c
    drc = vc
    dvc = Force(mc, mA, rc, rA)/mc
    
    #47d
    drd = vd
    dvd = Force(md, mA, rd, rA)/md
    
    return np.concatenate((drA, dvA, drB, dvB, drb, dvb, drc, dvc, drd, dvd))

In [5]:
###### 4th ORDER RUNGE-KUTTA METHOD ######
n = 1000
dt = pc/n #using period of 47c as it has the longest orbitabl period
tmax = pc + 40*day
t = 0
y = y0

###### POSITION ARRAYS ######
Ax, Ay = [], []
Bx, By = [], []
bx, by = [], []
cx, cy = [], []
dx, dy = [], []

while(t < tmax):
    Ax.append(y[0])
    Ay.append(y[1])
    Bx.append(y[4])
    By.append(y[5])
    bx.append(y[8])
    by.append(y[9])
    cx.append(y[12])
    cy.append(y[13])
    dx.append(y[16])
    dy.append(y[17])
    
    f1 = KeplerODE(t,        y)
    f2 = KeplerODE(t+dt/2.0, y+f1*dt/2.0)
    f3 = KeplerODE(t+dt/2.0, y+f2*dt/2.0)
    f4 = KeplerODE(t+dt    , y+f3*dt    )
    
    y += (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
    t += dt

In [6]:
###### FINDING HABITABLE ZONE ######
inner_rad = []
outer_rad = []
SL = 3.9E26 #solar luminosity in watts
AL = 0.84*SL #luminosity of 47A in watts
sf = SL/(4*np.pi*AU**2) #solar flux at earth = solar constant
for i in range(len(Ax)):
    x = np.abs(Ax[i])
    inner_rad.append(np.sqrt(AL/(4*np.pi*1.1*sf)) + x)
    outer_rad.append(np.sqrt(AL/(4*np.pi*0.53*sf)) + x)

In [7]:
###### FOLLOWING CODE USED TO MAKE ANIMATION 1 ######
fig = plt.figure(figsize = (8., 15.), dpi=200)
fig.clear()
with writer.saving(fig, "animation1.mp4", dpi=200):
    num_elements = len(Ax)
    angle = np.linspace(0, 2*np.pi, 150)
    for i in range (0,num_elements, 10):
        plt.clf()
        plt.xlim(min(cx)-AU/2, max(cx)+AU/2)
        plt.ylim(min(cy)-AU/2, max(cy)+AU/2)
        plt.gca().set_aspect('equal', adjustable='box')
        plt.title("Kepler-47 System")
        plt.xlabel("Distance(meters)")
        plt.ylabel("Distance(meters)")
        
        #plot the planets and stars
        plt.plot(Ax[0:i+1], Ay[0:i+1], '-c', linewidth = 0.5, label='47A')
        plt.plot(Bx[0:i+1], By[0:i+1], '-r', linewidth = 0.5, label='47B')
        plt.plot(bx[0:i+1], by[0:i+1], '-b', label='47b')
        plt.plot(cx[0:i+1], cy[0:i+1], '-', color="darkgreen", label='47c')
        plt.plot(dx[0:i+1], dy[0:i+1], '-m', label='47d')
        
        plt.plot(bx[i], by[i], 'ob', markersize=3)
        plt.plot(cx[i], cy[i], 'o', color="darkgreen", markersize=3)
        plt.plot(dx[i], dy[i], 'om', markersize=3)
        plt.plot(0,0,'+k', markersize=2)
        plt.legend(bbox_to_anchor=(1,1), loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.005)
        writer.grab_frame()
    for i in range(5):
        writer.grab_frame() #powerpoint keeps cutting off my animations so i needed to grab extra frames

In [8]:
###### FOLLOWING CODE USED TO MAKE ANIMATION 2 ######
fig = plt.figure(figsize = (10., 15.), dpi=200)
fig.clear()
with writer.saving(fig, "animation2.mp4", dpi=200):
    num_elements = len(Ax)
    angle = np.linspace(0, 2*np.pi, 150)
    for i in range (0,num_elements//2, 3):
        plt.clf()
        plt.xlim(min(cx)-AU/2, max(cx)+AU/2)
        plt.ylim(min(cy)-AU/2, max(cy)+AU/2)
        plt.gca().set_aspect('equal', adjustable='box')
        plt.title("Movement of Habitable Zone")
        plt.xlabel("Distance(meters)")
        plt.ylabel("Distance(meters)")
        
        #plot the inner and outer radii of the habitable zone
        radius1 = inner_rad[i]
        x1 = Ax[i] + radius1 * np.cos(angle) 
        y1 = Ay[i] + radius1 * np.sin(angle) 
        plt.plot(x1, y1, '--', color="green", linewidth=0.5)
        radius2 = outer_rad[i]
        x2 = Ax[i] + radius2 * np.cos(angle) 
        y2 = Ay[i] + radius2 * np.sin(angle) 
        plt.plot(x2, y2, '--', color="green", linewidth=0.5)
        plt.fill_between(x2, y2, color="springgreen", alpha=0.2, label="Habitable Zone")
        plt.fill_between(x1, y1, color="white")
        
        #plot the planets and stars
        plt.plot(Ax[0:i+1], Ay[0:i+1], '-c', linewidth = 0.5, label='47A')
        plt.plot(Bx[0:i+1], By[0:i+1], '-r', linewidth = 0.5, label='47B')
        plt.plot(bx[0:i+1], by[0:i+1], '-b', label='47b')
        plt.plot(cx[0:i+1], cy[0:i+1], '-', color="darkgreen", label='47c')
        plt.plot(dx[0:i+1], dy[0:i+1], '-m', label='47d')
        
        plt.plot(bx[i], by[i], 'ob', markersize=3)
        plt.plot(cx[i], cy[i], 'o', color="darkgreen", markersize=3)
        plt.plot(dx[i], dy[i], 'om', markersize=3)
        plt.plot(0,0,'+k', markersize=2)
        plt.legend(bbox_to_anchor=(1,1), loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.005)
        writer.grab_frame()

In [9]:
#Decided not to submit this animation
###### FOLLOWING CODE USED TO MAKE ANIMATION 1 ######
# fig = plt.figure(figsize = (10., 15.), dpi=200)
# fig.clear()
# with writer.saving(fig, "animation1.mp4", dpi=200):
#     num_elements = len(Ax)
#     for i in range (0,num_elements, 10):
#         plt.clf()
#         plt.xlim(min(cx)-AU/100, max(cx)+AU/100)
#         plt.ylim(min(cy)-AU/100, max(cy)+AU/100)
#         plt.gca().set_aspect('equal', adjustable='box')
#         plt.title("Kepler-47 System")
#         plt.xlabel("Distance(meters)")
#         plt.ylabel("Distance(meters)")
#         plt.plot(Ax[0:i+1], Ay[0:i+1], '-c', label='47A')
#         plt.plot(Bx[0:i+1], By[0:i+1], '-r', label='47B')
#         plt.plot(bx[0:i+1], by[0:i+1], '-b', label='47b')
#         plt.plot(cx[0:i+1], cy[0:i+1], '-g', label='47c')
#         plt.plot(dx[0:i+1], dy[0:i+1], '-m', label='47d')
        
#         plt.plot(Ax[i], Ay[i], '*c', markersize=3)
#         plt.plot(Bx[i], By[i], '*r', markersize=3)
#         plt.plot(bx[i], by[i], 'ob', markersize=3)
#         plt.plot(cx[i], cy[i], 'og', markersize=3)
#         plt.plot(dx[i], dy[i], 'om', markersize=3)
#         plt.plot(0,0,'+k', markersize=2)
#         plt.legend(bbox_to_anchor=(1,1), loc='upper left')
#         plt.draw()
#         plt.show()
        
#         plt.pause(0.005)
#         writer.grab_frame()

In [10]:
#Decided not to submit this animation
###### FOLLOWING CODE USED TO MAKE ANIMATION 2 ######
# fig = plt.figure(dpi=200)
# fig.clear()
# with writer.saving(fig, "animation2.mp4", dpi=200):
#     handles, labels = plt.gca().get_legend_handles_labels()
#     line1 = Line2D([0], [0], label='47A', color='cyan', linestyle='', marker='*')
#     line2 = Line2D([0], [0], label='47B', color='red', linestyle='', marker='*')
#     line6 = Line2D([0], [0], label='center of mass', color='black', linestyle='', marker='+')
#     handles.extend([line1, line2, line6])
#     num_elements = len(Ax)
#     plt.xlim(min(Bx)-AU/100, max(Bx)+AU/100)
#     plt.ylim(min(By)-AU/100, max(By)+AU/100)
#     plt.gca().set_aspect('equal', adjustable='box')
#     plt.title("Kepler-47 Stars Only")
#     plt.xlabel("Distance(meters)")
#     plt.ylabel("Distance(meters)")
#     for i in range (0,num_elements, 10):
#         plt.plot(Ax[i], Ay[i], '*c', markersize=5)
#         plt.plot(Bx[i], By[i], '*r', markersize=3)
#         plt.plot(0,0,'+k', markersize=2)
#         plt.draw()
#         plt.show()
#         plt.pause(0.3)
#         plt.legend(handles = handles, bbox_to_anchor=(1,1), loc='upper left')
#         writer.grab_frame()